### DMIs ordered

In [1]:
import json
import zipfile
import string
import toyplot
import numpy as np
import pandas as pd

### Zip archives with SLiM DMI result files


In [2]:
# archives with json files containing allele freqs x generation
Z100 = "test_mutation_order/Ne100_24genes.zip"
Z1000 = "test_mutation_order/Ne1000_24genes.zip"

# files containing genotype x generation (v. big files)
G100 = "test_mutation_order/test_Mutation-Order_Ne100_24genesinfoHybs.json"
G1000 = "test_mutation_order/test_Mutation-Order_Ne1000_24genesinfoHybs.json"

### Function to extract the simulation DMIs and genotypes


In [3]:
def extract_hybrids_from_json(file, seed):
    """
    This will extract the hybrid genotypes from a single seeded simulation.
    It returns the list of predefined DMIs, and a list of the F1 genotypes.
    e.g.,: ["AB", "cA", "DE", ...], ['aabBccdd', 'aabBccdd', 'aabBccdd', ...]
    """
    with open(file) as sdata:
        data = json.load(sdata)
   
    # get max generation from file
    maxgen = max([i["generation"] for i in data])   
   
    hybrids = []    
    
    # subset only last generation of a particular seed
    for run in data:
        if run["s"] == seed and run["generation"] == maxgen:
            
            # drop irrelevant key/vals from dict
            dmis = run['dmi']
            for key in ["generation", "s", "dmi"]:
                run.pop(key)
            
            # append genotypes by their frequency
            for genotype in run:
                hybrids += ([genotype] * run[genotype])  
    dmis = dmis.split("-")
    return dmis, hybrids

In [4]:
# example
dmis, hybrids = extract_hybrids_from_json(G100, "2719812637")

print(dmis[:10], '...')
print(hybrids[0])
print(hybrids[1])
print('...')

['BA', 'Ca', 'CB', 'Da', 'DB', 'Dc', 'EA', 'Eb', 'EC', 'ED'] ...
ABCDEFGHIJKlMNopQrstuVWxaBcdEFGHIjklMNOpqRsTuVWX
ABCDEFGHIJKlMNopQrstuVWxaBcdEFGHIjklMNOpqRsTuVWX
...


### Function to count DMIs in F1s

In [5]:
# def old_get_f1_dmis_from_hybrids(hybrids, dmis):
#     """
#     Takes a list of diploid hybrid genotypes and computes DMIs from dmi list. 
#         hybrids = ['AAbbCCDD', 'AAbbCCdD', ...]
#         dmis = ["AB", "aC", "BC", "aD", "BD", "cD"]
#     returns a list of integers.
#     """
#     counts = []
#     for hybrid in hybrids:
#         count = 0
#         for dmi in dmis:
#             c0 = hybrid.count(dmi[0])
#             c1 = hybrid.count(dmi[1])
#             count += (c0 * c1)
#         counts.append(count)
#     return counts

In [6]:
def get_f1_dmis_from_hybrids(hybrids, dmis):
    """
    Takes a list of diploid hybrid genotypes and computes DMIs from dmi list. 
        hybrids = ['AAbbCCDD', 'AAbbCCdD', ...]
        dmis = ["AB", "aC", "BC", "aD", "BD", "cD"]
    returns a list of integers.
    """
    counts = []
    for hybrid in hybrids:
        count = 0
        for dmi in dmis:
            if dmi[0] in hybrid and dmi[1] in hybrid:
                count += 1
        counts.append(count)
    return counts

In [7]:
dmis, hybrids = extract_hybrids_from_json(G100, "2719812637")
ndmis = get_f1_dmis_from_hybrids(hybrids, dmis)
print("n_dmis: {}".format(ndmis[:10]))

n_dmis: [131, 131, 131, 131, 131, 131, 131, 131, 131, 131]


### Function to extract order of fixation from json

In [8]:
def extract_order_of_fixation(data):
    """
    From a JSON input file with allele frequencies x generation,
    Returns the sequence of P2 and P3 fixation (paths): 
    input = {"G": ..., "ABcdE": '1', "abCDe": '2', ...}
    e.g., [ACD, B]
    """
    order2 = []
    order3 = []
    for gdict in data:
        for key in gdict:
            # store fix 2
            if key.endswith("2"):
                if gdict[key] == 1:
                    if (key != "G") and (key[0] not in order2):
                        order2.append(key[0])

            # store fix 3
            if key.endswith("3"):
                if gdict[key] == 1:
                    if (key != "G") and (key[0] not in order3):
                        order3.append(key[0])

    return order2, order3

### For each zip json get order of fixation and count final DMIs

In [9]:
def get_order_data(zipres, genofile, ninds=1000):

    # store results
    path1 = []
    path2 = []
    avgdmis = []
    stddmis = []
    
    # iterate over files in zipdir
    with zipfile.ZipFile(zipres, 'r') as zipdir: 
        for zipf in zipdir.filelist:
            if zipf.filename.endswith(".json"):

                # extract Json data
                sdata = zipdir.read(zipf)
                data = json.loads(sdata)
                
                # store order of fixation
                orders = extract_order_of_fixation(data)
                path1.append("".join(orders[0]))
                path2.append("".join(orders[1]))
                                
                # get predefined DMI list and 100 F1 genotypes
                seed = zipf.filename.split("alleleFreq")[0].split("genes")[-1]
                dmis, hybrids = extract_hybrids_from_json(genofile, seed)
                
                # count DMIs in the 100 
                dmilist = get_f1_dmis_from_hybrids(hybrids, dmis)
                avgdmis.append(np.mean(dmilist))
                stddmis.append(np.std(dmilist))
                
    # organize into a dataframe
    df = pd.DataFrame({
        "path1": path1,
        "path2": path2,
        "mean_dmis": avgdmis,
        "std_dmis": stddmis,
    })
    return df

In [10]:
res100 = get_order_data(Z100, G100)

In [11]:
res1000 = get_order_data(Z1000, G1000)

In [13]:
res100.head()

path1             path2  mean_dmis   std_dmis
0   KAHDGCJPRUQSLB  BHOFECALGMNIWVTX     219.42   4.819087
1    BGMETFHIVNWXO    FMECOBGNDVWITX      59.63  15.181999
2  LAKGCHBRDQSEJPU    BFAINEOWXMTGVJ     226.09   3.919426
3    KLCADFHJRUPSQ  OKEMALUCJBHDSPRQ      83.21  10.998450
4     KACHJPLDURSQ   CADPLJHKSRQBEUF      50.63  11.890042

In [14]:
res1000.head()

path1         path2  mean_dmis   std_dmis
0    BEAFIGMOTN       CEADBJH    132.625  22.030124
1  BAEFIMGNOVTW  CADHKLJPRQSU    258.049   7.554509
2  CADHJLKPQRSU  ADHCKJLPQSRU     21.646  18.716856
3  ACJHDKLPQRSU  BFEIGMNOTVWX    268.641   7.462581
4  ADCHJKLPQRSU  ACDHJLKPQSUR     21.550  17.595440

In [19]:
res100.mean_dmis.median(), res100.mean_dmis.std()

(131.1, 73.32739538569814)

In [20]:
res1000.mean_dmis.median(), res1000.mean_dmis.std()

(98.0535, 107.2167877293929)

### Graph of ordered paths
This only shows that both follow a consistent path starting either on `A-C-D` or on `B-`.

In [21]:
def plot_order_graph(res, ngenes=24, width=None, height=None, max_dmis=None, axes=None):

    # concatenated 
    res = pd.concat([res.path1, res.path2])
    max_dmis = (max_dmis if max_dmis else res.apply(len).max())
    
    # setup canvas and axes
    if not axes:
        canvas = toyplot.Canvas(
            width=(width if width else min(700, 50 * max_dmis)),
            height=(height if height else min(700, 75 * ngenes)),
        )
        axes = canvas.cartesian()
    else:
        canvas = None
    axes.x.label.text = "Rank order of fixation"
    axes.y.label.text = "Gene"        
        
    # record frequency on each path 
    sizes = np.zeros((ngenes, max_dmis))
    
    # add network connections
    for dat in res:

        opacity = 0.05
        if dat[0] in ["A", "C", "D"]:
            color = toyplot.color.Palette()[0]
        elif dat[0] in ["B", "E", "F"]:
            color = toyplot.color.Palette()[1]
        else:
            color = "grey"
                
        xidx = 0
        for gidx in range(len(dat[1:max_dmis])):

            # get gene index and last gene index
            lidx = ngenes - string.ascii_uppercase.index(dat[gidx]) - 1
            gidx = ngenes - string.ascii_uppercase.index(dat[gidx + 1]) - 1

            # add line connecting points
            axes.plot(
                [xidx, xidx + 1], 
                [lidx + np.random.normal(0, 0.1), gidx + np.random.normal(0, 0.1)],
                opacity=opacity,
                color=color,
            )
            xidx += 1
            
        # record grid size data
        for idx, gene in enumerate(dat[:max_dmis]):
            gidx = string.ascii_uppercase.index(gene)
            sizes[gidx, idx] += 1
              
    # scale grid points to reflect relative frequency
    sizes += .001  # make all non-zero
    sizes = sizes / sizes.max(axis=0)
    sizes *= 8  # multiply to extend range of sizes
    sizes += 1  # add minimum size
    # if no data then set column size to smallest (2)
    sizes[:, np.all(sizes == 9.0, axis=0)] = 1
            
    # add grid points
    x, y = np.meshgrid(np.arange(max_dmis), np.arange(ngenes))
    axes.scatterplot(
        x.flatten(), 
        y.flatten(), 
        size=sizes[::-1].flatten(), 
        opacity=0.6, 
        mstyle={
            "fill": "none",
            #"fill": "#262626", 
            "stroke": "#262626",
            "stroke-width": 2},
    );
    axes.y.ticks.locator = toyplot.locator.Explicit(
        labels=list(string.ascii_uppercase)[:ngenes][::-1])
    axes.x.ticks.locator = toyplot.locator.Explicit(labels=range(1, max_dmis + 1))

    # styling axes
    axes.y.ticks.labels.angle = -90
    #axes.y.ticks.labels.style["font-size"] = "10px"
    axes.y.ticks.labels.style['text-anchor'] = 'middle'
    axes.y.ticks.labels.offset = 12
    axes.x.domain.min = -0.25
    axes.y.domain.min = -0.25
    
    return canvas, axes

In [78]:
def plot_rates(axes):

    d0 = pd.read_csv("test_mutation_order/ind+sel_f100_m5r6_100i_24g_final_timeComparison(1).csv")
    d1 = pd.read_csv("test_mutation_order/ind+sel_f100_m5r6_1000i_24g_final_timeComparison(1).csv")
    d2 = pd.read_csv("test_mutation_order/ind+sel_f100_m5r6_10000i_24g_final_timeComparison(1).csv")

    text_heights = (112, 65, 32)
    text_texts = ("Ne=100", "Ne=1000", "Ne=10000")

    for idx, dat in enumerate((d0, d1, d2)):
        
        # add in the point at (0, 0) that was not recorded but is inherent
        # to the simulation.
        dat.loc[-1] = [0, 0, 0]    # adding a row
        dat.index = dat.index + 1  # shifting index
        dat = dat.sort_index()     # sorting by index

        #axes.scatterplot(
        axes.plot(
            dat.iloc[:, 0], 
            dat.iloc[:, 1],
            color="black",
        );
        axes.fill(
            dat.iloc[:, 0], 
            dat.iloc[:, 1] - dat.iloc[:, 2], 
            dat.iloc[:, 1] + dat.iloc[:, 2], 
            opacity=0.1,
            color="#262626",
        )
        axes.text(    
            3500,
            text_heights[idx],
            text_texts[idx],
            style={
                "text-anchor": "end", 
                "fill": "#262626", 
                "opacity": 0.8,
                "font-size": "10px",
            }
        )

    axes.x.ticks.locator = toyplot.locator.Explicit(range(0, 4000, 1000))
    axes.x.label.text = "Generations"
    axes.y.label.text = "DMIs in F1 hybrids"
    axes.y.ticks.locator = toyplot.locator.Extended(5, only_inside=True)
    return axes

In [79]:
dd = plot_rates(toyplot.Canvas().cartesian())

<svg class="toyplot-canvas-Canvas" height="600px" id="tf03f2828c85a472797f165476cdbdd03" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 600 600" width="600px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 50.0 537.2704793635857 L 55.1413881748072 485.7184451196425 L 60.13996001142531 465.9364642850172 L 65.13853184804341 454.0122822393588 L 70.13710368466153 443.3467048766395 L 75.13567552127964 433.24994884240436 L 80.13424735789775 424.2704072426581 L 85.13281919451585 418.23217116345813 L 90.13139103113396 407.96295906446727 L 95.12996286775208 399.27555067078276 L 100.1285347043702 389.2984453101919 L 105.12710654098828 383.61246974583344 L 110.12567837760639 376.7847755046151 L 115.1242502142245 372.69287501595693 L 120.12282205084263 365.941696378372 L 125.12139388746071 362.830061830605 L 130.11996572407884 359.6541830495985 L 135.11853756069695 352.17009079985013 L 140.11710939731506 346.6691482518258 L 145.11568123393317 342.27984749244087 L 150.11425307055129 337.6150424369537 L 155.11282490716937 333.2271853682032 L 160.11139674378748 328.20025457853825 L 165.1099685804056 328.1020836153856 L 170.1085404170237 324.4055137455012 L 175.10711225364184 316.54509947033466 L 180.10568409025996 313.1396738784273 L 185.10425592687804 308.26649614134675 L 190.10282776349615 304.9807910014642 L 195.10139960011426 306.4818539018796 L 200.09997143673237 303.2908163692098 L 205.09854327335046 299.7759109041787 L 210.09711510996857 296.28070219170576 L 215.09568694658668 293.53194890954865 L 220.0942587832048 288.69896833203745 L 225.0928306198229 286.21399417187865 L 230.09140245644102 283.3692523055786 L 235.08997429305913 280.7660519132015 L 240.08854612967724 279.66594040043054 L 245.08711796629535 277.1205237257033 L 250.08568980291346 273.82822573192277 L 255.08426163953158 271.61480015552746 L 260.0828334761497 268.8548029294781 L 265.0814053127678 267.90067260137516 L 270.0799771493859 265.7698718461489 L 275.07854898600397 263.2385961211875 L 280.0771208226221 260.9242469448295 L 285.07569265924025 259.83268448676637 L 290.07426449585836 259.24410865809875 L 295.0728363324764 256.13498853818703 L 300.0714081690946 253.51295038917976 L 305.0699800057126 253.93334107121905 L 310.06855184233075 250.78104738287965 L 315.06712367894886 248.7748804401379 L 320.065695515567 248.2561166782573 L 325.0642673521851 246.55029513513716 L 330.0628391888032 243.7711305097624 L 335.0614110254213 245.65381378022488 L 340.0599828620395 245.1522564045576 L 345.05855469865753 245.14984303504662 L 350.05712653527564 244.32551252574928 L 355.0556983718937 245.2333725690134 L 360.0542702085118 243.1035150250016 L 365.05284204513 244.78116294538756 L 370.05141388174803 242.03377876318234 L 375.0499857183662 242.82076099576267 L 380.04855755498426 243.24123829923988 L 385.0471293916024 241.18236702373122 L 390.04570122822054 240.4380602863098 L 395.0442730648386 239.3065268468768 L 400.0428449014567 239.20465281724648 L 405.0414167380749 239.6719369772485 L 410.0399885746929 239.9922558367995 L 415.0385604113111 238.58499192306505 L 420.03713224792915 238.93952625065583 L 425.0357040845473 236.98552947514636 L 430.0342759211654 235.60806814841206 L 435.0328477577835 237.33784292531135 L 440.0314195944016 236.79997191788195 L 445.02999143101965 235.38347079023697 L 450.0285632676378 234.76107650845378 L 455.02713510425593 234.43930914596595 L 460.02570694087404 233.0127623376554 L 465.02427877749216 232.60271088671087 L 470.02285061411027 231.45541475169904 L 475.0214224507284 231.30186140965225 L 480.01999428734655 230.58906081418007 L 485.01856612396455 230.27351575832705 L 490.01713796058266 229.734747256

In [80]:
# https://github.com/dlukes/rbo
from rbo.rbo import *

In [81]:
def fill_homoplasy(res):
    res = res.copy()
    res["homoplasy_rbo"] = 0
    for idx in res.index:
        path1 = res.loc[idx, "path1"]
        path2 = res.loc[idx, "path2"]
        est = rbo(path1, path2, 0.9).ext
        res.loc[idx, "homoplasy_rbo"] = est
    return res

In [82]:
c = toyplot.Canvas(975, 350)

axes = c.cartesian(bounds=(50, 250, 50, 300))#, label="Ne=100")
plot_order_graph(res100, 24, max_dmis=15, axes=axes)

axes = c.cartesian(bounds=(325, 525, 50, 300))#, label="Ne=1000")
plot_order_graph(res1000, 24, max_dmis=15, axes=axes);

axes = c.cartesian(bounds=(600, 725, 50, 300))
plot_rates(axes);
axes.x.ticks.show = True
axes.y.ticks.show = True

ax0 = c.cartesian(bounds=(800, 925, 50, 140))
ax1 = c.cartesian(bounds=(800, 925, 210, 300))

x = fill_homoplasy(res100)
ax0.scatterplot(
    x.homoplasy_rbo, x.mean_dmis, 
    size=5, 
    mstyle={
        "stroke-opacity": 0.5, 
        "fill-opacity": 0.5, 
        "fill": "#262626",
        "stroke": "262626",
    },
)
ax0.x.label.text = "Homoplasy (rbo)"
ax0.y.domain.min = 0
ax0.y.domain.max = 325
ax0.x.ticks.locator = toyplot.locator.Explicit([0, 0.5, 1.0], ['0.0', '0.5', '1.0'])
ax0.x.ticks.show = True
ax0.y.ticks.show = True

x = fill_homoplasy(res1000)
ax1.scatterplot(
    x.homoplasy_rbo, x.mean_dmis, 
    size=6, 
    mstyle={
        "stroke-opacity": 0.5, 
        "fill-opacity": 0.5, 
        "fill": "#262626",
        "stroke": "none",
    },
)#, opacity=0.5)

ax1.x.label.text = "Homoplasy (rbo)"
ax1.y.domain.min = 0
ax1.y.domain.max = 325
ax1.x.ticks.locator = toyplot.locator.Explicit([0, 0.5, 1.0], ['0.0', '0.5', '1.0'])
ax1.x.ticks.show = True
ax1.y.ticks.show = True

c.text(765, 175, "DMIs in F1 Hybrids", angle=90, style=ax0.x.label.style)
c.text(
    800, 135, "Ne=100", 
    style={
        "text-anchor": "start", 
        "fill": "#262626", 
        "opacity": 0.8, 
        "font-size": "10px",
    })
c.text(
    800, 295, "Ne=1000", 
    style={
        "text-anchor": "start",
        "fill": "#262626", 
        "opacity": 0.8,
        "font-size": "10px",
    });

<svg class="toyplot-canvas-Canvas" height="350.0px" id="t70d92d406fc644dba0c2c598f48d159c" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 975.0 350.0" width="975.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 151.75438596491227 274.61756948407293 L 165.78947368421052 285.89668091350165" style="stroke:rgb

In [83]:
import toyplot.pdf
import toyplot.svg
# toyplot.pdf.render(c, "./figures/Fig-3-composite.pdf")
toyplot.svg.render(c, "./figures/Fig-3-std-raw-composite.svg")

### DMIs versus homoplasy

In [29]:
x = fill_homoplasy(res100)

In [140]:
c, a, m = toyplot.scatterplot(
    x.homoplasy_rbo, x.mean_dmis, 
    size=5, 
    width=250, 
    height=205,
    xlabel="homoplasy (rank biased overlap)", 
    ylabel="mean N DMIs in F1s",
);

a.y.ticks.show = True
a.x.ticks.show = True

<svg class="toyplot-canvas-Canvas" height="205.0px" id="td2e0f986d7ca4ef1828493e0ce6a1405" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 250.0 205.0" width="250.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 0.0 0.5 1.0 homoplasy (rank biased overlap) 0 100 200 300 mean N DMIs in F1s

In [71]:
h24K.sort_values(by="homoplasy_rbo")

path1         path2    dmis  homoplasy_rbo
45  BEIFGNMTOVWX  ACDHJLKQPURS   6.218       0.000000
30  ACDHJKLPRQSU  EBFIGMONXTVW   6.373       0.000000
33  CADHJKPLQURS  BEGFMINOVTWX   6.114       0.000000
57  DAHCKJLPQRSU  BFEIGONMTWVX   6.299       0.000000
52  BEGFIMNOVTWX  ADCHKJLPQSRU   6.412       0.000000
..           ...           ...     ...            ...
98  ACHDKJPLQRUS  ADCKHJPLQRSU   0.654       0.906605
24  BEFGIMNTOWVX   BFEGNIMOTVW   1.600       0.912178
11  ACJHDKLPQRSU  ACDJKHLPQSRU   0.876       0.937779
4   ADCHJKLPQRSU  ACDHJLKPQSUR   0.516       0.938114
67  ABDCHJKLPQRS   ABDJCHKLPQR  12.000       0.958647

[100 rows x 4 columns]

In [67]:
h24 = fill_homoplasy(res24)
h24K = fill_homoplasy(res24K)

In [69]:
toyplot.scatterplot(h24.homoplasy_rbo, h24.dmis, size=6, width=400, height=400, xlabel="homoplasy", ylabel="dmis");
toyplot.scatterplot(h24K.homoplasy_rbo, h24K.dmis, size=6, width=400, height=400);

<svg class="toyplot-canvas-Canvas" height="400.0px" id="tc8e3e0727f8a4e11a6f4b14e80c4150d" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 400.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 0.0 0.2 0.4 0.6 0.8 homoplasy 0 5 10 15 dmis

<svg class="toyplot-canvas-Canvas" height="400.0px" id="t5c3ab20669b3458c924900a82287aa28" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 400.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 0.0 0.5 1.0 0 4 8 12

In [7]:
rbo([{"a", "c"}, "b", "d"], ["a", {"b", "c"}, "d"], p=.9)

RBO(min=0.48919503099801515, res=0.47747163566865164, ext=0.9666666666666667)

### Plot of homoplasy vs avg. DMIs

In [29]:
res24

path1             path2    dmis
0     KAHDGCJPRUQSLB  BHOFECALGMNIWVTX  10.122
1      BGMETFHIVNWXO    FMECOBGNDVWITX   9.228
2    LAKGCHBRDQSEJPU    BFAINEOWXMTGVJ   9.111
3      KLCADFHJRUPSQ  OKEMALUCJBHDSPRQ   6.264
4       KACHJPLDURSQ   CADPLJHKSRQBEUF   6.288
..               ...               ...     ...
95   HAECFGDJLBKRQPS     HBEIFJOGNMTVW   9.385
96    FADHBJMIEVNGCO   BNACJRKDHLQPSUE  12.000
97   IFOCADPMNKTBWEG   EBFJOCGAINMHVWT  10.132
98      AJKDHPCULQSR      AHKJCQLDRPSU   0.762
99  GAJREDKBHCFPLQUS     FDAHKCJMBEOQP  12.000

[100 rows x 3 columns]

In [22]:
def plot_homoplasy(res, ngenes, **kwargs):
    
    # create copy of df
    test = res.copy()
    test['homoplasy'] = 0

    # fill homoplasy column
    for idx in test.index:
        set1 = test.loc[idx, 'path1']
        set2 = test.loc[idx, 'path2']
        homoplasy = [i for i in set1 if i in set2]
        test.loc[idx, 'homoplasy'] = len(homoplasy)
        
    # plot scatter markers
    canvas, axes, mark = toyplot.scatterplot(
        test.homoplasy, 
        test.dmis, 
        width=min(700, 75 * ngenes), 
        height=275, 
        size=12,
        opacity=0.25,
        marker="-",
        mstyle={"stroke-width": 3},
        xlabel="N genes fixed in both lineages (homoplasy)",
        ylabel="Avg. DMIs in F1 hybrids",
        **kwargs,
    );
    
    # add homoplasy counters
    axes.text(
        range(ngenes),
        [test.dmis[test.homoplasy == i].max() + 0.3 for i in range(ngenes)],
        [len(test.dmis[test.homoplasy == i]) for i in range(ngenes)],  
        color="#262626",
        style={"font-size": "10px"}
    )

    return canvas, axes

In [23]:
plot_homoplasy(res100, 4);

<svg class="toyplot-canvas-Canvas" height="275.0px" id="t287d1cd902484bdd81edb4c2d5b18baa" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 300.0 275.0" width="300.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 37 11 2 50 0 1 2 3 N genes fixed in both lineages (homoplasy) 0 2 4 6 Avg. DMIs in F1 hybrids

In [24]:
plot_homoplasy(res1000, 4);

<svg class="toyplot-canvas-Canvas" height="275.0px" id="tf03d0c3443e54860a7d60f7dc9c9a175" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 300.0 275.0" width="300.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 11 1 7 81 0 1 2 3 N genes fixed in both lineages (homoplasy) 0 2 4 6 Avg. DMIs in F1 hybrids

In [25]:
c, a = plot_homoplasy(res24, 24);
a.x.domain.max = 15

<svg class="toyplot-canvas-Canvas" height="275.0px" id="tc215233ed80a4022818026abce2aa11c" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 700.0 275.0" width="700.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 0 1 4 3 6 10 11 4 8 1 5 8 25 10 4 0 0 0 0 0 0 0 0 0 0 5 10 15 N genes fixed in both lineages (homoplasy) 0 5 10 15 20 Avg. DMIs in F1 hybrids